Before you turn this problem in, make sure everything runs as expected. First, **restart the kernel** (in the menubar, select Kernel$\rightarrow$Restart) and then **run all cells** (in the menubar, select Cell$\rightarrow$Run All).

Make sure you fill in any place that says `YOUR CODE HERE` or "YOUR ANSWER HERE", as well as your name below.

Rename this problem sheet as follows:

    ps{number of lab}_{your user name}_problem{number of problem sheet in this lab}
    
for example
    
    ps2_blja_problem1

Submit your homework within one week until next Monday, 9 a.m.

In [ ]:
NAME = ""
EMAIL = ""
USERNAME = ""

---

# Introduction to Data Science
## Lab 11: Subset selection

In this and the following labs, we want to explore different methods of linear model selection.

In the lecture you've learned about problems that might occur in datasets with many predictors (high $p$)and a low number of samples (low $n$).
Ways out could be:
* Subset selection - try to find a suitable subset of predictors
* Skrinkage/Regularization - increase weights of *important* predictors, decrease weights of *unimportant* ones
* Dimension reduction - Build linear combinations $v_i, i=1,\ldots,M$ of predictors and fit a model using these vectors instead of predictors with $M < p$

We always have to keep in mind that it's in general not wise to select the model with the minimal training error, due to the danger of overfitting.
Our goal is to find a model that performs well on a test set.
This refers to a subset of samples that are completely held out from training (and also cross-validation).

### Part A - Best subset selection

We want to implement the **best subset selection** algorithm from the lecture:
1. Let $\mathcal{M}_0$ denote the *null model*, which contains no predictors.
2. For $k = 1, 2, \ldots, p$:
  1. Fit all $p \choose k$ models that contain exactly $k$ predictors.
  2. Pick the best among these and call it $\mathcal{M}_k$, while the best is the one with highest $R^2$ score.
3. Select a single best model from among $\mathcal{M}_0, \ldots \mathcal{M}_p$ using one of the following methods:
    * cross-validated prediction error
    * $C_p$ (or equivalently AIC - Akaike information criterion)
    * BIC - Bayesian information criterion
    * adjusted $R^2$


### Understanding steps 1 and 2
    
The algorithm `bestSubsetComputation` belows contains the implementation of step 1 and step 2.

**Task (no points)**: Understand the following code and add comments as you wish.

In [ ]:
import numpy as np

from itertools import combinations

from sklearn.linear_model import LinearRegression
from sklearn.metrics import r2_score

def bestSubsetComputation(X, y, scoring_func = r2_score):
    """ Input: X - predictor array of size (n,p)
               y - array of size (n,)
               scoring_func - function that takes two arguments y_true
                  and y_pred, and returns a score
               
    """
    
    # Get the number of samples and the number of predictors 
    n, p = X.shape
    
    # Prepare lists that keep the best scores and models:
    #     best_score[i] keeps the best score in a model i predictors
    #     best_model[i] keeps the best model using i predictors
    
    best_score = []
    best_model = []

    ### First step in best subset selection algorithm
    
    # The model containing no predictors simply predicts the sample mean
    ybar = y.mean()
    yhat = ybar * np.ones_like(y)

    best_score.append(scoring_func(y, yhat))
    best_model.append( () )
    
    ### Second step in best subset selection algorithm

    # Loop over k - number of predictors in our model
    for k in range(1,p+1):

        best_model.append( () )
        best_score.append(0.)

        for l in combinations(range(p),k):

            lr = LinearRegression()
            lrfit = lr.fit(X[:,l],y)
            yhat = lrfit.predict(X[:,l])

            this_score = scoring_func(y,yhat)
            
            if this_score > best_score[k]:
                best_score[k] = this_score
                best_model[k] = l
                
    return (best_model, best_score)

**Task (1 point)**: Load the diabetes data set form `sklearn`.
If you forgot how to do this have a look at the previous labs.

Store the predictors in an array `X`, and the targets in an array `y`.

In [ ]:
# YOUR CODE HERE
raise NotImplementedError()

In [ ]:
assert type(X) == np.ndarray
assert abs(X.mean()) < 1e-12
assert abs(y.mean() - 152.13348416289594) <1e-10
assert X.shape == (442,10)
assert y.shape == (442,)

**Task (1 point)**: Use the function `train_test_split` from `sklearn.model_selection` to split the data into a training and test set `X_train`, `y_train` and `X_test`, `y_test`.
Use as `test_size=0.2` and `random_state=1`.

In [ ]:
# YOUR CODE HERE
raise NotImplementedError()

In [ ]:
assert abs(X_train[3,4] + 0.0469754041408486) < 1e-6
assert abs(y_test[5] - 178) < 1e-6
assert X_test.shape == (89,10)
assert y_train.shape == (353,)

**Task (1 point)**:
Apply the `bestSubsetComputation` function from above to the training set.
Store the list of best models in a variable `best_models` and the corresponding maximum scores in `best_scores`.

In [ ]:
# YOUR CODE HERE
raise NotImplementedError()

In [ ]:
assert abs(np.mean([sum(i) for i in best_models]) - 21.90909090909091) < 1e-8
assert (np.mean([i[0] for i in best_models[1:]]) - 1.2) < 1e-8
assert abs(np.var(best_scores) - 0.023162490321673723) < 1e-8

**Task (no points)**: Now, you can execute the following cell.

In [ ]:
import matplotlib.pyplot as plt
%matplotlib inline
plt.rcParams['figure.figsize'] = (15,8)
plt.plot(range(len(best_score)), best_score, 'r+-')
plt.xlabel('Number of predictors')
plt.ylabel('R^2 score')

for i,s in enumerate(best_score):
    print('\nScore of model with %i predictors has score %6.4f' % (i,s))
    print('\tSelected predictors', best_model[i])

### Implementing step 3 of the *best subset selection* algorithm

In the following tasks, you should implement step 3 of the *best subset selection* algorithm using the **training data** from the diabetes data set.

In the lecture you've learned about the performance criteria:
* AIC
    $$ AIC = \frac{1}{n \hat \sigma^2} (RSS + 2 d {\hat \sigma}^2)$$
* BIC
    $$ BIC = \frac{1}{n} (RSS + \log(n) d {\hat \sigma}^2)$$
* Adjusted R^2
    $$ R^2_{Adj} = 1 - \frac{RSS / (n - d - 1)}{TSS / (n - 1)} $$
  
with $d$ being the number of parameters in the model and $\hat{\sigma}^2$  referring to an estimate of the variance associated with each response in the linear model (estimated on a model containing all predictors):
    $$ {\hat \sigma}^2 = \frac{1}{n - p - 1} \sum_{i=1}^n (y_i - \hat y_i)^2.  $$

**Task (1 point)**: Implement the function `RSS` to compute the residual sum of squares for input `y` and corresponding `yhat`.

**Remember**: $TSS$ is the total sum of squares, which is defined by 
$\sum_{i=1}^n (y_i - \hat y_i)^2$.

In [ ]:
def RSS(y, yhat):
    """ This function return the residual sum of squares
    for inputs of size (n,). """
    # YOUR CODE HERE
    raise NotImplementedError()

In [ ]:
assert abs(RSS(y,np.ones_like(y)) - 12716877) < 1e-10

**Task (1 point)**: Implement the function `TSS` to compute the total sum of squares for an input `y`.

**Remember**: $TSS$ is the total sum of squares, which is defined by $\sum_{i=1}^n (y_i - \bar y)^2$.

In [ ]:
def TSS(y):
    """ This function return the total sum of squares
    for an input of size (n,). """
    # YOUR CODE HERE
    raise NotImplementedError()

In [ ]:
assert abs(TSS(y) - 2621009.124434389) < 1e-10
np.random.seed(0)
assert abs(TSS(np.random.randn(1000)) - 974.2344563121542) < 1e-10

**Task (2 points)**: Implement a function `sigmaHat` that takes the input `X` and `y` and returns the estimate of sigma, i.e., $\hat \sigma$.
Then, compute $\hat \sigma$ for your training data and store its value in the variable `shat_dia`.

*Hint*: Within the function, you might have to perform a linear regression fit. Use also the function `RSS` if necessary.

In [ ]:
# Implement the function sigmaHat
# YOUR CODE HERE
raise NotImplementedError()

# Evaluate the function for your training data
# YOUR CODE HERE
raise NotImplementedError()

In [ ]:
assert abs(shat_dia - 54.09455498707545) < 1e-10

Below, you find an implementation of the Akaike Information Criterion (AIC).

**Task (2 points)**: Complete the implementations of the functions `BIC` and `adjustedRSquare` that take as arguments `y`, `yhat`, `d`, and `shat`, if necessary.

In [ ]:
def AIC(y, yhat, d, shat):
    n = len(y)
    return (RSS(y,yhat) + 2 * d * shat**2) / (n * shat**2)

def BIC(y, yhat, d, shat):
    # YOUR CODE HERE
    raise NotImplementedError()

def adjustedRSquare(y, yhat, d):
    # YOUR CODE HERE
    raise NotImplementedError()

In [ ]:
assert abs(AIC(y_train, y_train, 3, 5) - 0.0169971671388102) < 1e-10
assert abs(BIC(y_train, y_train, 3, 5) - 1.2464167259773293) < 1e-10
assert abs(adjustedRSquare(y_train, y_train, 3) - 1) < 1e-10

**Task (2 points)**: Use the return values of the function `bestSubsetComputation`, in particular the variable `best_models`, to perform step 3 of the *best subset selection* algorithm using the training data from the diabetes data set.

Store the scores for the three criteria (adjusted $R^2$, AIC and BIC) in the corresponding lists `R2score`, `AICscore` and `BICscore`, resp.

In [ ]:
n,p = X_train.shape

R2score = []
AICscore = []
BICscore = []

# YOUR CODE HERE
raise NotImplementedError()

In [ ]:
assert abs(np.mean(R2score) - 0.44973260288515904) < 1e-8
assert abs(np.mean(AICscore) - 1.1561158131306397) < 1e-8
assert abs(np.mean(BICscore) - 3543.307165450913) < 1e-8

**Task (1 point)**: For each of the considered criteria, select and store the index that optimizes the criterion as `R2idx`, `AICidx` and `BICidx`, resp.

In [ ]:
# YOUR CODE HERE
raise NotImplementedError()

In [ ]:
assert R2idx + AICidx + BICidx == 18

**Task (3 points)**: Plot the scores against the number of predictors in seperate plots.
Highlight the point that optimizes the respective criterion.

In [ ]:
import matplotlib.pyplot as plt
plt.rcParams['figure.figsize'] = (15,8)
fig, ax = plt.subplots(1,3)

# YOUR CODE HERE
raise NotImplementedError()

Below, you can find an implementation of the best subset selection algorithm as one function `bestSubsetSelection`.
Since it employs your implemented functions, e.g. `BIC`, `adjustedRSquare`, etc., it's a further check for the correctness of your implementation.

**Task (1 point)**: Read the code thoroughly and add comments as you wish. Make sure that the following assert statements are passed.

In [ ]:
def bestSubsetSelection(X, y, scoring = 'aic'):
    """ Input: X - predictor array of size (n,p)
               y - array of size (n,)
               scoring - string, either 'aic', 'bic' or 'r2'
        Output: (best_score, best_model) - best parameter selection
    """
    score = []
    def scoring_func(y, yhat, d):
        if scoring == 'r2':
            return adjustedRSquare(y, yhat, d)
        else:
            shat = sigmaHat(X,y)      
            if scoring == 'aic':
                return AIC(y, yhat, d, shat)
            elif scoring == 'bic':
                return BIC(y, yhat, d, shat)
            else:
                raise NameError('scoring not known')

    best_model, best_score = bestSubsetComputation(X, y)
    
    for d, l in enumerate(best_model):
        if d == 0:
            yhat = y.mean() * np.ones_like(y)
        else:
            lr = LinearRegression()
            lrfit = lr.fit(X[:,l],y)
            yhat = lrfit.predict(X[:,l])

        score.append( scoring_func(y, yhat, d) )
        
    if scoring == 'r2':
        best_idx = np.argmax(score)
    else:
        best_idx = np.argmin(score)
    
    return score[best_idx], best_model[best_idx]

In [ ]:
# Test the implementation
R2_score, R2_model = bestSubsetSelection(X_train,y_train,'r2')
assert abs(R2_score - 0.5225204821123409) < 1e-10
assert R2_model == (1, 2, 3, 4, 5, 7, 8)

AIC_score, AIC_model = bestSubsetSelection(X_train,y_train,'aic')
assert abs(AIC_score - 1.0090748842464763) < 1e-10
assert AIC_model == (1, 2, 3, 4, 6, 8)

BIC_score, BIC_model = bestSubsetSelection(X_train,y_train,'bic')
assert abs(BIC_score - 3114.815511092917) < 1e-10
assert BIC_model == (1, 2, 3, 6, 8)

### Part B: Forward and backward stepwise selection algorithm

**Task (5 points)**: Once you've done Part A of this lab, it should be rather easy to implement either the **forward stepwise selection algorithm** or the **backward stepwise selection algorithm** as a function `forwardStepwiseSelection` or `backwardStepwiseSelection`, resp.

Start by implementing a function `forwardStepwiseComputation` or `backwardStepwiseComputation` to perform steps 1 and 2 of the respective algorithm.

Use 10-fold cross-validation as a measure for model selection (step 3 of the algorithms).
Here, you can use the function `cross_val_score` from `sklearn.model_selection`.

In [ ]:
# YOUR CODE HERE
raise NotImplementedError()

In [ ]:
from sklearn.datasets import load_diabetes
data = load_diabetes()

#print(data.DESCR)
X = data.data
y = data.target

if 'forwardStepwiseSelection' in locals():
    fSS_score, fSS_model = forwardStepwiseSelection(X,y)
elif 'backwardStepwiseSelection' in locals():
    fBB_score, fBB_model = backwardStepwiseSelection(X,y)
else: assert False, 'Implement the backwardStepwiseSelection or the forwardStepwiseSelection'

assert 'fSS_score' in locals() and abs(fSS_score - 0.4723839929236253) < 1e-8 or 'fBB_score' in locals() and abs(fBB_score - 0.4723839929236256) < 1e-8

if 'forwardStepwiseSelection' in locals():
    np.random.seed(0)
    fSS_score, fSS_model = forwardStepwiseSelection(np.random.randn(100,10),np.random.randn(100,))
    assert abs(fSS_score + 0.11591245146628207) < 1e-6
    assert fSS_model[1] == 4
elif 'backwardStepwiseSelection' in locals():
    np.random.seed(1)
    bSS_score, bSS_model = backwardStepwiseSelection(np.random.randn(100,10),np.random.randn(100,))
    assert abs(bSS_score + 0.17226717542216358) < 1e-6
    assert bSS_model[1] == 3
    
else:
    assert False, 'Implement the backwardStepwiseSelection or the forwardStepwiseSelection'